In [1]:
import os 
import cv2
import numpy as np
import clip
import torch
from PIL import Image
from tqdm import tqdm
import pathlib
from pathlib import Path
import glob
import argparse
import json
import jsonlines
import json_numpy
import pandas as pd
import pyarrow as pa
import time
import fastparquet

/scratch/bbki/kastanday/conda_envs/envs/v3_clip_preprocessing_yt1b/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

# read pandas
df = pd.read_pickle('/scratch/bbki/kastanday/whisper/old.pickle')
df

del df['frame_embeddings']
del df['text_caption_embeddings']
del df['segment_frames']
df

video_stem  \
0   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
1   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
2   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
3   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
4   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
5   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
6   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
7   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
8   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
9   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
10  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
11  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
12  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
13  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
14  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
15  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
16  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
17  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
18  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
19  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
20  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
21  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
22  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
23  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
24  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
25  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
26  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   
27  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...   

                                           segment_id  segment_index  \
0   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              0   
1   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              1   
2   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              2   
3   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              3   
4   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              4   
5   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              5   
6   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              6   
7   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              7   
8   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              8   
9   qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...              9   
10  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             10   
11  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             11   
12  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             12   
13  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             13   
14  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             14   
15  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             15   
16  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             16   
17  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             17   
18  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             18   
19  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             19   
20  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             20   
21  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             21   
22  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             22   
23  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             23   
24  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             24   
25  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             25   
26  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             26   
27  qLfp0gjvhJo_Club86_8687_Rich's 1993 Defender ｜...             27   

    num_frames_per_segment  total_segments  segment_total_time  \
0                        3              28            3.139313   
1                        3              28            4.706938   
2                        3              28            3.331625   
3                        3          

In [4]:
# write panda to parquet
fastparquet.write('shouldntworkbutmight.parquet', df)

: 

: 

In [3]:
# read parquet
parss = "shouldntworkbutmight.parquet"
clip_outputs =  fastparquet.ParquetFile(parss).to_pandas()
clip_outputs

TypeError: 'NoneType' object is not iterable

In [5]:
import fastparquet
parss = "/scratch/bbki/kastanday/whisper/parallel_14_clip_output.parquet"
clip_outputs =  fastparquet.ParquetFile(parss).to_pandas()
clip_outputs

video_stem  \
0    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...   
1    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...   
2    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...   
3    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...   
4    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...   
..                                                 ...   
429  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...   
430  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...   
431  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...   
432  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...   
433  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...   

                                            segment_id  segment_index  \
0    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...              0   
1    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...              1   
2    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...              2   
3    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...              3   
4    XTMAMXG7mk4_Rob Anderson_788649_Giving $35,000...              4   
..                                                 ...            ...   
429  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...             98   
430  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...             99   
431  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...            100   
432  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...            101   
433  y8G0k197YiI_Martial Arts Unlimited_2345_Venom ...            102   

     num_frames_per_segment  total_segments  segment_total_time  \
0                         1              80            3.474125   
1                         1              80            3.020625   
2                         1              80            3.485313   
3                         1              80            3.955312   
4                         1              80            4.477062   
..                      ...             ...                 ...   
429                       1             103            3.259750   
430                       1             103            3.644187   
431                       1             103            3.680125   
432                       1             103            3.493250   
433                       1             103            4.313625   

                                              captions  segment_start_time  \
0    HI I'M ROB ANDERSON LAS VEGAS MAGICIAN LAST MO...            4.132937   
1    TRICK WHERE I RIPPED UP A HOMELESS MAN'S SIGN ...            7.667000   
2    PILE OF MONEY FOR IT THAT VIDEO WENT VIRAL WIT...           10.727500   
3    APPEARED EVERYWHERE FROM CNN TO THE TODAY SHOW...           14.252313   
4    OVER FORTYZERO IN ONE MONTH FOR ALAN THE HOMEL...           18.246813   
..                                                 ...                 ...   
429  PUNCHER KEY THE VENOM-D AND THEN I HAD THE FIG...          505.343375   
430  BY THE RASH GUARD AND THEN I HAVE TWO OF THE G...          508.591813   
431  YOU HAVE IT THANKS FOR WATCHING IF YOU HAVEN'T...          512.224438   
432  THAT LIKE BUTTON AND THAT SUBSCRIBE BUTTON YOU...          515.912750   
433  AND DON'T FORGET TO HIT THAT BELL ICON AS YOU ...          520.180875   

     segment_end_time                                   frame_embeddings  \
0            7.607063  b'\x10\xab\xed\xb5\xb37\xae<Q\xb1\xa3\xb4\xff\...   
1           10.687625  b'6\xb4\x01\xb4\xed7\xd8<+-Q\xb9z\xa9&8m7\xbf\...   
2           14.212813  b'\xea\xb8\xad0\xe3*\x15=\xb6\xb0\xfa\xb4\xe1\...   
3           18.207625  b'\xaa\xb5c\xaf\xa65\xbf=\xec\xab\xf52\x9f\xb7...   
4           22.723875  b'G3c\xb5 8\xe39\x0b\xb5^\xae\xfd\xbb\xf07\x8e...   
..                ...                                                ...   
429        508.603125  b'b0\xeb\xba 9\xf3\xae\xd5\xb9l\xb7\xc8/\xd6\x...   
430        512.236000  b'Q.\x00\xba\x179\x1c\xb8,\xba\xc7\xb6\xc01\xa...   
431        515.904562  b'\xcf05\xbd\x05:q\xb

[1, 2, 3, 21, 22, 23]


In [100]:
def list_to_dict(lst):
  {k: v for v, k in enumerate(lst)}

In [7]:
data = np.array([[1,2,3,], [21,22,23]])

arr = pa.array(data)
arr

ArrowInvalid: only handle 1-dimensional arrays

In [39]:
image_feature = np.array([[1,2,3,], [21,22,23]])
# print(dict(enumerate(image_feature)))
one_segment_output = pd.DataFrame({
  "frame_embeddings": image_feature.tobytes(),
  "frame_embeddings_TWOOOO": image_feature.tobytes(),
}, index=[0])
two_segment_output = pd.DataFrame({
  "frame_embeddings": image_feature.tobytes(),
  "frame_embeddings_TWOOOO": image_feature.tobytes(),
}, index=[0])
# one_segment_output

In [40]:
list_of_segment_outputs = [one_segment_output, two_segment_output]

segments_of_entire_video = pd.concat(list_of_segment_outputs, ignore_index=True)
segments_of_entire_video

frame_embeddings  \
0  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...   
1  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...   

                             frame_embeddings_TWOOOO  
0  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...  
1  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...

In [41]:
import fastparquet
fastparquet.write('test_pandas.parquet', segments_of_entire_video)

In [42]:
import fastparquet
parss = "test_pandas.parquet"
test_outputs =  fastparquet.ParquetFile(parss).to_pandas()
test_outputs

frame_embeddings  \
0  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...   
1  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...   

                             frame_embeddings_TWOOOO  
0  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...  
1  b'\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00...

In [105]:
l1=['a','b','c','d']
d1=
print (d1)#Output:{0: 'a', 1: 'b', 2: 'c', 3: 'd'}

{0: 'a', 1: 'b', 2: 'c', 3: 'd'}


In [104]:
flatten(image_feature)

[1, 2, 3, 21, 22, 23]

In [82]:
table = pa.Table().from_pydict({'a': [1, 2, 3], 'b': [4, 5, 6]})


print(table)

TypeError: Do not call Table's constructor directly, use one of the `Table.from_*` functions instead.

In [84]:
video_filepath = '/tmp/hello.py'
i = 9
# one_segment_output = pa.Table.from_pandas(pd.DataFrame({
#                 "video_stem": [str(Path(video_filepath).stem), 'hi'],
#                 "segment_id": [str(Path(video_filepath).stem) + f"_{i}", 'hi'],
#                 "segment_index": [i, i],
# }))

# df = pd.DataFrame()
list_ofTihgsn = []
for i in range(5):
  one_segment_output = pd.DataFrame({
                  "video_stem": "VERSION 2",
                  "segment_id": "VERSION_2" + f"_{i}",
                  "segment_index": {"segment": [69,69,69]},
  }, index=[0])
  list_ofTihgsn.append(one_segment_output)

segs = pd.concat(list_ofTihgsn, ignore_index=True)
fastparquet.write('outfile.parq',segs, append=True)

In [54]:
two_segment_output = {
                "video_stem": str(Path(video_filepath).stem),
                "segment_id": str(Path(video_filepath).stem) + f"_{i}",
                "segment_index": i,
}
one_segment_output = {
                "video_stem": "str(Path(video_filepath).stem)",
                "segment_id": "str(Path(video_filepath).stem)" + f"_{i}",
                "segment_index": 10,
}

In [55]:
list_of_segment_outputs = [one_segment_output, two_segment_output]

In [67]:
# one_video_of_segments = pa.concat_tables(*list_of_segment_outputs)
one_video_of_segments = pa.Table.from_pylist(list_of_segment_outputs)
one_video_of_segments

pyarrow.Table
video_stem: string
segment_id: string
segment_index: int64
----
video_stem: [["str(Path(video_filepath).stem)","hello"]]
segment_id: [["str(Path(video_filepath).stem)_9","hello_9"]]
segment_index: [[10,9]]

In [63]:
import pyarrow.parquet as pq

In [25]:
from fastparquet import ParquetFile
pf = ParquetFile('outfile.parq')
df = pf.to_pandas()
df

TypeError: int() argument must be a string, a bytes-like object or a number, not 'NAType'

In [81]:
list_of_filepaths = list(df['segment_id'])
list_of_filepaths

['str(Path(video_filepath).stem)_9',
 'VERSION_2_9',
 'VERSION_2_0',
 'VERSION_2_1',
 'VERSION_2_2',
 'VERSION_2_3',
 'VERSION_2_4']

In [75]:
import fastparquet

fastparquet.write('outfile.parq',one_segment_output, append=True)

# pyarrow.parquet.write_table('test_parquet_append.parquet', one_video_of_segments, append=False, schema=None, index=None)

In [2]:
video_data_path = '/scratch/bbki/kastanday/whisper/parallel_1'
video_input_dir = Path(video_data_path)
output_path = str(os.path.join(video_input_dir.parent, video_input_dir.stem + '_clip_output.jsonl'))
audio_jsonl = str(os.path.join(video_input_dir.parent, video_input_dir.stem + '_whisper_output.jsonl'))
audio_jsonl

'/scratch/bbki/kastanday/whisper/parallel_14_whisper_output.jsonl'

In [5]:
debug = True
video_dir_files = set()
stem_to_filename = {}
start_time = time.monotonic()

# GLOB VIDEOS
# for video_dir_file in glob.glob(os.path.join(video_data_path, '*'), recursive = True):
#     # print(Path(video_dir_file).stem)
#     video_dir_files.add(str(Path(video_dir_file).stem))
#     stem_to_filename[str(Path(video_dir_file).stem)] = video_dir_file
# print(f"Globbing from scratch 25k video files: {time.monotonic() - start_time}:2f seconds")

# FIND WHISPER JSON OBJS
start_time = time.monotonic()
audio_file_stems = []
stem_to_whisper = {}  # filename.stem --> whisper_json_object
one_json = None

df = pd.DataFrame()
with jsonlines.open(audio_jsonl) as reader:
    try:
        for idx, obj in enumerate(reader):
            json_objs = json.loads(obj)
            for json_obj in json_objs:
                audio_file_stems.append(json_obj['video_filename_stem'])

                if json_obj['video_filename_stem'] not in stem_to_whisper:
                    stem_to_whisper[json_obj['video_filename_stem']] = []
                
                stem_to_whisper[json_obj['video_filename_stem']].append(json_obj)
                
                one_json = json_obj
                
                df['video_filename_stem'] = json_obj
                if idx > 0:
                    break
    except Exception as e:
        print(f"Error: couldn't read {audio_jsonl}. Got error: {e}")
if debug:
    print(f"Done collecting {audio_jsonl}")

print(f"JsonL parsing time: {time.monotonic() - start_time:2f} seconds")
# stem_to_whisper
df

Done collecting /scratch/bbki/kastanday/whisper/parallel_14_whisper_output.jsonl
JsonL parsing time: 34.829023 seconds


video_filename_stem
caption              I'M GOING ON EVERYONE HOW ARE YOU GUYS DOING O...
start                                                            4.008
end                                                          13.631562
segment_word_list    [{'word': 'I'M', 'start': 4.008, 'end': 4.3286...
video_filename_stem    u5DEHtDBqeI_The Grooming Guy_1076_got2b Shampoo
video_filepath       /tmp/parallel_14/u5DEHtDBqeI_The Grooming Guy_...

In [17]:
one_json['np_test'] = [1] * 512
one_json['segment_word_list'] = 'penis'

In [24]:
# thing  =np.zeros((512))

df2 = pd.DataFrame(one_json)
df2

NameError: name 'one_json' is not defined

In [ ]:
all_whisper = []
with jsonlines.open(audio_jsonl) as reader:
    try:
        for _, obj in enumerate(reader):
            json_objs = json.loads(obj)
    except Exception as e:
        print(f"Error: couldn't read {audio_jsonl}. Got error: {e}")

In [30]:
from pyarrow import json
import pandas as pd
start_time = time.monotonic()
# table = json.read_json(str(audio_jsonl))
# table = jsonlines.read_json(str('small.jsonl'))
df2 = pd.read_json(str(audio_jsonl), lines=True, encoding='utf-8')
print(f"JsonL --> pyarrow parsing time: {time.monotonic() - start_time:2f} seconds")
df2

JsonL --> pyarrow parsing time: 15.658412 seconds


0
0      [{"caption": "THE NEW AT FIVE A STUDENT GOT SE...
1      [{"caption": "I DIDN'T KNOW WHAT TO GET ANYONE...
2      [{"caption": "IT'S TIME FOR A JOKE A JOKE FROM...
3      [{"caption": "HEY Y'ALL MY NAME IS RAVANNA AND...
4      [{"caption": "A BRAND NEW SEASON OF JAYLON'S B...
...                                                  ...
19558  [{"caption": "WE'RE HERE TODAY BECAUSE WE'VE B...
19559  [{"caption": "I'M GOING TO GO BACK TO THERE WI...
19560  [{"caption": "I'M SORRY MAJOR DO YOU BRING ANY...
19561  [{"caption": "SO WELCOME BACK TO THE WIFE MOTH...
19562  [{"caption": "OKAY SO I WAS ABLE TO PUT MY CAM...

[19563 rows x 1 columns]

In [28]:
df2[0]


'[{"caption": "THE NEW AT FIVE A STUDENT GOT SENT HOME FROM ROSDALE MIDDLE SCHOOL AFTER BRINGING", "start": 0.0601875, "end": 4.2144375, "segment_word_list": [{"word": "THE", "start": 0.0601875, "end": 0.1404375}, {"word": "NEW", "start": 0.1805625, "end": 0.32099999999999995}, {"word": "AT", "start": 0.3611875, "end": 0.4414375}, {"word": "FIVE", "start": 0.481625, "end": 0.8026875}, {"word": "A", "start": 0.842875, "end": 0.9030625}, {"word": "STUDENT", "start": 0.94325, "end": 1.284375}, {"word": "GOT", "start": 1.3044375, "end": 1.4649375}, {"word": "SENT", "start": 1.4850625, "end": 1.6857499999999999}, {"word": "HOME", "start": 1.7259375, "end": 1.9266249999999998}, {"word": "FROM", "start": 1.96675, "end": 2.12725}, {"word": "ROSDALE", "start": 2.1674375, "end": 2.5888750000000003}, {"word": "MIDDLE", "start": 2.6290625, "end": 2.8498124999999996}, {"word": "SCHOOL", "start": 2.8899375, "end": 3.1708749999999997}, {"word": "AFTER", "start": 3.6124375, "end": 3.813125}, {"word": 

In [9]:
!head -n1 '/scratch/bbki/kastanday/whisper/parallel_13_whisper_output.jsonl'

"[{\"caption\": \"HOMEWARD BOUND IS A PROGRAM THAT WAS STARTED OUT OF AUSTRALIA AND ITS INTERNATIONAL LEADERSHIP\", \"start\": 2.247625, \"end\": 7.2059999999999995, \"segment_word_list\": [{\"word\": \"HOMEWARD\", \"start\": 2.247625, \"end\": 2.5285625}, {\"word\": \"BOUND\", \"start\": 2.548625, \"end\": 3.251}, {\"word\": \"IS\", \"start\": 3.351375, \"end\": 3.4516875}, {\"word\": \"A\", \"start\": 3.491875, \"end\": 3.5721249999999998}, {\"word\": \"PROGRAM\", \"start\": 3.873125, \"end\": 4.1540625}, {\"word\": \"THAT\", \"start\": 4.1741875, \"end\": 4.254437500000001}, {\"word\": \"WAS\", \"start\": 4.2745, \"end\": 4.35475}, {\"word\": \"STARTED\", \"start\": 4.3949375, \"end\": 4.655812500000001}, {\"word\": \"OUT\", \"start\": 4.6959375, \"end\": 4.796250000000001}, {\"word\": \"OF\", \"start\": 4.8364375, \"end\": 4.896624999999999}, {\"word\": \"AUSTRALIA\", \"start\": 5.1374375, \"end\": 5.6993125}, {\"word\": \"AND\", \"start\": 5.7194375, \"end\": 5.7996875}, {\"word\"

# Try loading parallel_10_clip_output.jsonl


In [1]:
import jsonlines
import pprint

In [2]:
import jsonlines

inpath = '/scratch/bbki/kastanday/whisper/parallel_10_clip_output.jsonl'
json_result = []
with jsonlines.open(inpath) as reader:
  for _, obj in enumerate(reader):
    json_result.append(obj)
    break
  
pprint.pprint(json_result)

[{'captions': "IT'S HARD TO BELIEVE BUT EVEN LARGE LIFT TRUCKS CAN BE "
              'INVISIBLE ESPECIALLY IN NOISY',
  'filename': 'HpM19evm4OA_WorkSafeBC_6928_Fields of Vision： Invisible Lift '
              'Truck (3 of 5)',
  'frame_embeddings': [[-0.12939453125,
                        0.1163330078125,
                        -0.0679931640625,
                        0.07708740234375,
                        0.52294921875,
                        0.23681640625,
                        0.409423828125,
                        0.2452392578125,
                        -0.1527099609375,
                        -0.0176849365234375,
                        0.34912109375,
                        -0.04638671875,
                        0.84619140625,
                        0.1016845703125,
                        -0.2491455078125,
                        0.148193359375,
                        -0.32666015625,
                        0.443603515625,
                        -0.099609375,
 

In [3]:
import pandas as pd

# image_feature = [[1,2,3,], [21,22,23]]
# print(dict(enumerate(json_result[0]['frame_embeddings'])))
one_segment_output = pd.DataFrame({
  "frame_embeddings": {"frame_embeddings": dict(enumerate(json_result[0]['frame_embeddings']))},
}, index=[0])
one_segment_output

frame_embeddings
0               NaN

In [7]:
len(json_result[0]['frame_embeddings'])

3

In [8]:
len(json_result[0]['frame_embeddings'][0])

512

In [9]:
import numpy as np
ar = np.ndarray(shape = (3,512), buffer = json_result[0]['frame_embeddings'])

TypeError: a bytes-like object is required, not 'list'

In [5]:
import json

# write json to disk: json_result[0] with name 'one_clip_output.json'
with open('one_clip_output.json', 'w') as outfile:
    json.dump(json_result[0], outfile)

In [12]:
import pyarrow
fn = 'one_clip_output.json'
table = pyarrow.json.read_json(fn, read_options=pyarrow.json.ReadOptions(use_threads = True, block_size = 3200024))

In [13]:
table

pyarrow.Table
filename: string
segment_length: double
captions: string
segment_start_time: double
segment_end_time: double
frame_embeddings: list<item: list<item: double>>
  child 0, item: list<item: double>
      child 0, item: double
text_caption_embeddings: list<item: list<item: double>>
  child 0, item: list<item: double>
      child 0, item: double
segment_frames: list<item: string>
  child 0, item: string
----
filename: [["HpM19evm4OA_WorkSafeBC_6928_Fields of Vision： Invisible Lift Truck (3 of 5)"]]
segment_length: [[6.3686875]]
captions: [["IT'S HARD TO BELIEVE BUT EVEN LARGE LIFT TRUCKS CAN BE INVISIBLE ESPECIALLY IN NOISY"]]
segment_start_time: [[8.27125]]
segment_end_time: [[14.6399375]]
frame_embeddings: [[[[-0.12939453125,0.1163330078125,-0.0679931640625,0.07708740234375,0.52294921875,...,0.08599853515625,0.38232421875,0.52294921875,0.0261993408203125,0.01629638671875],[0.026458740234375,0.141357421875,-0.0928955078125,0.050811767578125,0.151611328125,...,0.39013671875,0.4